In [1]:
import pandas as pd 
import numpy as np 
import matplotlib.pyplot as plt
import seaborn as sns 

In [63]:
billing = pd.read_csv("billing.csv") 
events = pd.read_csv("events.csv")
sessions = pd.read_csv("sessions.csv")
users = pd.read_csv('users.csv')

Looking into expansion events group and non expansion group and testing out what are their behvaiour. Make a test and control group that we want to study

In [33]:
expand_users = users[(users['expansion_event'] == 1 )]
# no_expand_users = users[(users['expansion_event'] == 0 )]
print(len(expand_users))
# print(len(no_expand_users))

69309


In [ ]:
tier_map = {'free':0, 'standard': 1, 'premium':2}
billing['prev_tier'] = billing['plan_tier'].shift()
# Map tiers to numbers
billing["tier_num"] = billing["plan_tier"].map(tier_map)
billing["prev_tier_num"] = billing["prev_tier"].map(tier_map)

# Compare current vs. previous
def change_type(row):
    if pd.isna(row["prev_tier_num"]):
        return "no_change"   # first row, no previous
    elif row["tier_num"] > row["prev_tier_num"]:
        return "upgrade"
    elif row["tier_num"] < row["prev_tier_num"]:
        return "downgrade"
    else:
        return "no_change"

billing["change"] = billing.apply(change_type, axis=1)



In [31]:
billing['prev_seat'] = billing['active_seats'].shift()
billing['change_seat'] = billing['active_seats'] - billing['prev_seat']
billing

user_id    month plan_tier  \
0        f94d1824-8742-4000-8b6d-39d70958490b  2024-05      free   
1        f94d1824-8742-4000-8b6d-39d70958490b  2024-06      free   
2        f94d1824-8742-4000-8b6d-39d70958490b  2024-07      free   
3        f94d1824-8742-4000-8b6d-39d70958490b  2024-08      free   
4        f94d1824-8742-4000-8b6d-39d70958490b  2024-09      free   
...                                       ...      ...       ...   
1000171  2bebcb3d-bead-492a-97e3-1346173ee638  2025-03      free   
1000172  2bebcb3d-bead-492a-97e3-1346173ee638  2025-04      free   
1000173  2bebcb3d-bead-492a-97e3-1346173ee638  2025-05      free   
1000174  2bebcb3d-bead-492a-97e3-1346173ee638  2025-06      free   
1000175  2bebcb3d-bead-492a-97e3-1346173ee638  2025-07      free   

         active_seats  mrr  discount_applied  invoices_overdue  \
0                   2  0.0                 0                 0   
1                   2  0.0                 0                 0   
2                   1  0.0                 0                 0   
3                   1  0.0                 0                 0   
4                   1  0.0                 0                 0   
...               ...  ...               ...               ...   
1000171             4  0.0                 0                 0   
1000172             2  0.0                 0                 0   
1000173             2  0.0                 0                 0   
1000174             3  0.0                 0                 0   
1000175             3  0.0                 0                 0   

         support_ticket_count prev_tier  tier_num  prev_tier_num     change  \
0                           0      None         0            NaN  no_change   
1                           0      free         0            0.0  no_change   
2                           0      free         0            0.0  no_change   
3                           0      free         0            0.0  no_change   
4                           0      free         0            0.0  no_change   
...                       ...       ...       ...            ...        ...   
1000171                     0      free         0            0.0  no_change   
1000172                     0      free         0            0.0  no_change   
1000173                     0      free         0            0.0  no_change   
1000174                     0      free         0            0.0  no_change   
1000175                     0      free         0            0.0  no_change   

         prev_seat  change_seat  
0              NaN          NaN  
1              2.0          0.0  
2              2.0         -1.0  
3              1.0          0.0  
4              1.0          0.0  
...            ...          ...  
1000171        5.0         -1.0  
1000172        4.0         -2.0  
1000173        2.0          0.0  
1000174        2.0          1.0  
1000175        3.0          0.0  

[1000176 rows x 14 columns]

In [68]:
# 1. Sort by user_id and month
billing = billing.sort_values(["user_id", "month"])
# 2. High-Water Mark: cumulative max per user
billing["max_seats_to_date"] = billing.groupby("user_id")["active_seats"].cummax()
# 3. Previous High-Water Mark: shift within each user’s history
billing["prev_max_seats_to_date"] = billing.groupby("user_id")["max_seats_to_date"].shift()
# 4. True Expansion Month condition
billing["true_expansion_month"] = billing["active_seats"] > billing["prev_max_seats_to_date"]


In [105]:
# users[(~users.isin(expansion_events['user_id'].uniq)) & (users['churned_90d'] == False) & (users['dowgraded'] == False)]
# 1. Identify non-expansion users
# non_expand_users = users[
#     (~users["user_id"].isin(expansion_events["user_id"].unique()))
#     & (users["churned_90d"] == False)
#     & (users["downgraded"] == False)
# ]

# # 2. Anchor date for each user: let's use their latest billing month
# last_activity = (
#     billing[billing["user_id"].isin(non_expand_users["user_id"])]
#     .groupby("user_id", as_index=False)
#     .agg(last_month=("month", "max"))
# )

# # convert to datetime if not already
# last_activity["last_month"] = pd.to_datetime(last_activity["last_month"])

# # 3. Define pre-"window" of ~60 days prior to last_month
# last_activity["window_start"] = last_activity["last_month"] - pd.Timedelta(days=60)
# last_activity["window_end"]   = last_activity["last_month"]

# # Assuming 'users' is your users.csv DataFrame
# # And 'expansion_group_ids' is the list of user_ids for your expansion group

# 1. Create the signup_month column
users['signup_date'] = pd.to_datetime(users['signup_date'])
users['signup_month'] = users['signup_date'].dt.to_period('M')

# 2. Isolate the expansion group's matching data
expansion_users_df = users[users['user_id'].isin(expansion_events["user_id"].unique())].copy()

# 3. Create the control pool
# Start with users who are NOT in the expansion group
control_pool_df = users[~users['user_id'].isin(expansion_events["user_id"].unique())].copy()
# Filter for stable users (not churned or downgraded)
control_pool_df = control_pool_df[
    (control_pool_df['churned_90d'] == False) &
    (control_pool_df['downgraded'] == False)
]


In [106]:
control_pool_df

user_id signup_date plan_tier  \
1      238bf0af-1f71-45e4-a47d-dcb5db33f71b  2025-04-11  standard   
7      3ea81032-dd9b-4ce2-bdf4-6a99c01fcff0  2025-05-12      free   
9      12de9c20-5bd4-4251-adde-dd07eaa82e8c  2024-12-27      free   
10     904f47f7-6f21-41b9-b031-86dd264376b3  2025-05-04      free   
17     cca57714-3aab-4644-9b5d-a7166c408368  2025-06-06      free   
...                                     ...         ...       ...   
99973  271d311a-49d5-45a4-abc2-b05b189e5f38  2024-06-21   premium   
99979  8906fae6-a894-4874-9bb2-4f3493219ce4  2024-12-21      free   
99990  e34dbe71-5343-415b-84c3-7d01751704f9  2025-02-03      free   
99991  17475b9e-2885-4ba1-97f8-5c32335c5419  2025-05-14  standard   
99993  7c29b911-02b3-485d-9704-06db4e49ae5e  2025-04-18  standard   

      company_size region   industry acquisition_channel  is_enterprise  \
1             1-10    NaN  education                 seo          False   
7             200+    NaN     energy            outbound          False   
9            11-50     EU    finance                 seo          False   
10          51-200    NaN  transport             partner          False   
17          51-200    NaN  transport             partner          False   
...            ...    ...        ...                 ...            ...   
99973         1-10   APAC  transport                 seo          False   
99979       51-200    NaN     retail                 seo          False   
99990        11-50    NaN      media                 seo          False   
99991         1-10    NaN      media            outbound          False   
99993         1-10    NaN     energy             partner          False   

       churned_30d  churned_90d  downgraded  expansion_event signup_month  
1                0            0           0                0      2025-04  
7                0            0           0                0      2025-05  
9                0            0           0                1      2024-12  
10               0            0           0                0      2025-05  
17               0            0           0                0      2025-06  
...            ...          ...         ...              ...          ...  
99973            0            0           0                1      2024-06  
99979            0            0           0                0      2024-12  
99990            0            0           0                1      2025-02  
99991            0            0           0                1      2025-05  
99993            0            0           0                0      2025-04  

[20940 rows x 13 columns]

In [ ]:
import pandas as pd
import random

# A list to store the user_ids of the matched controls we find
matched_control_ids = []

# A list to store expansion users for whom we successfully found a match.
# This is important if some expansion users have no possible twin.
matched_expansion_ids = []

# Make a copy of the pool to safely modify it
control_pool_for_matching = control_pool_df.copy()

# Loop through each user in our expansion group
print("Starting the matching process...")
for index, user in expansion_users_df.iterrows():
    # Get the characteristics of the expansion user
    user_id = user['user_id']
    plan = user['plan_tier']
    size = user['company_size']
    industry = user['industry']
    signup = user['signup_month']

    # Search for potential twins in the remaining control pool
    potential_matches = control_pool_for_matching[
        (control_pool_for_matching['plan_tier'] == plan) &
        (control_pool_for_matching['company_size'] == size) &
        (control_pool_for_matching['industry'] == industry) &
        (control_pool_for_matching['signup_month'] == signup)
    ]

    # Check if we found any matches
    if not potential_matches.empty:
        # A match was found! Randomly select one.
        matched_twin = potential_matches.sample(n=1)
        matched_twin_id = matched_twin.iloc[0]['user_id']

        # Add the twin to our list of successful matches
        matched_control_ids.append(matched_twin_id)
        
        # Add the original expansion user to our list of successfully matched users
        matched_expansion_ids.append(user_id)

        # CRITICAL: Remove the selected twin from the pool so they can't be chosen again
        control_pool_for_matching.drop(matched_twin.index, inplace=True)
    else:
        # No match was found for this expansion user.
        # We will have to exclude them from the final comparison.
        print(f"Warning: No match found for expansion user {user_id}. They will be excluded.")

print("Matching process complete.")

# 4. Create your final, matched DataFrames
final_expansion_group = expansion_users_df[expansion_users_df['user_id'].isin(matched_expansion_ids)]
final_control_group = control_pool_df[control_pool_df['user_id'].isin(matched_control_ids)]

Starting the matching process...
Matching process complete.


In [ ]:
# Save expansion group
final_expansion_group.to_csv("final_expansion_group.csv", index=False)

# Save control group
final_control_group.to_csv("final_control_group.csv", index=False)


In [120]:
#5e9df73e-052e-402d-abdf-940f20f4d440
# billing[billing['user_id'] == '5e9df73e-052e-402d-abdf-940f20f4d440']
expansion_events = billing[billing['true_expansion_month'] == True]
first_expansion_dates = (
    expansion_events
    .groupby("user_id", as_index=False)
    .agg(first_expansion_month=("month", "min"))
)

# 3. Define pre-expansion window
# If 'month' is stored as a string like 'YYYY-MM', convert to datetime (first day of month)
first_expansion_dates["first_expansion_month"] = pd.to_datetime(first_expansion_dates["first_expansion_month"])

# The pre-expansion window is simply the prior calendar month
first_expansion_dates["pre_expansion_start"] = (first_expansion_dates["first_expansion_month"] - pd.offsets.MonthBegin(1))
first_expansion_dates["pre_expansion_end"]   = (first_expansion_dates["first_expansion_month"] - pd.offsets.MonthEnd(1))


In [121]:
first_expansion_dates

user_id first_expansion_month  \
0      0000093e-7258-43c0-b212-ea7212795ddf            2025-01-01   
1      0003c565-9352-45aa-a448-82b91e57b043            2025-04-01   
2      00044174-f9c1-4412-b9ca-584a21903f92            2025-03-01   
3      0006fdbd-c35d-4c0d-a948-e8ee10f279d5            2025-03-01   
4      0007ee13-0c60-4865-9464-914b2df654df            2025-07-01   
...                                     ...                   ...   
72493  fff8e699-03db-42d2-aad8-cefaf815a92d            2025-01-01   
72494  fffa9cdd-f19a-4849-ae3b-2302b5b68020            2024-03-01   
72495  fffcb715-b3de-4a0e-813a-df5dd2f833d2            2025-06-01   
72496  fffce54a-cd86-4f93-b529-d92586690bd5            2025-02-01   
72497  fffea094-3414-40c4-bab2-3925ba64491d            2025-07-01   

      pre_expansion_start pre_expansion_end  
0              2024-12-01        2024-12-31  
1              2025-03-01        2025-03-31  
2              2025-02-01        2025-02-28  
3              2025-02-01        2025-02-28  
4              2025-06-01        2025-06-30  
...                   ...               ...  
72493          2024-12-01        2024-12-31  
72494          2024-02-01        2024-02-29  
72495          2025-05-01        2025-05-31  
72496          2025-01-01        2025-01-31  
72497          2025-06-01        2025-06-30  

[72498 rows x 4 columns]

In [122]:
billing[billing['user_id']== '0000093e-7258-43c0-b212-ea7212795ddf']

user_id    month plan_tier  active_seats  \
202639  0000093e-7258-43c0-b212-ea7212795ddf  2024-10      free             1   
202640  0000093e-7258-43c0-b212-ea7212795ddf  2024-11      free             1   
202641  0000093e-7258-43c0-b212-ea7212795ddf  2024-12      free             1   
202642  0000093e-7258-43c0-b212-ea7212795ddf  2025-01      free             3   
202643  0000093e-7258-43c0-b212-ea7212795ddf  2025-02      free             4   
202644  0000093e-7258-43c0-b212-ea7212795ddf  2025-03      free             4   
202645  0000093e-7258-43c0-b212-ea7212795ddf  2025-04      free             3   
202646  0000093e-7258-43c0-b212-ea7212795ddf  2025-05      free             4   
202647  0000093e-7258-43c0-b212-ea7212795ddf  2025-06      free             3   
202648  0000093e-7258-43c0-b212-ea7212795ddf  2025-07      free             3   

        mrr  discount_applied  invoices_overdue  support_ticket_count  \
202639  0.0                 0                 0                     0   
202640  0.0                 0                 0                     0   
202641  0.0                 0                 0                     0   
202642  0.0                 0                 0                     0   
202643  0.0                 0                 0                     0   
202644  0.0                 0                 0                     0   
202645  0.0                 0                 0                     0   
202646  0.0                 0                 0                     0   
202647  0.0                 0                 0                     0   
202648  0.0                 0                 0                     0   

        max_seats_to_date  prev_max_seats_to_date  true_expansion_month  
202639                  1                     NaN                 False  
202640                  1                     1.0                 False  
202641                  1                     1.0                 False  
202642                  3                     1.0                  True  
202643                  4                     3.0                  True  
202644                  4                     4.0                 False  
202645                  4                     4.0                 False  
202646                  4                     4.0                 False  
202647                  4                     4.0                 False  
202648                  4                     4.0                 False